In [1]:
from sequence_aligner.labelset import LabelSet
from sequence_aligner.dataset import  TrainingDataset
from sequence_aligner.containers import TrainingBatch
import json
from transformers import XLMRobertaTokenizerFast, XLMRobertaForTokenClassification, TrainingArguments, Trainer
from torch.utils.data import random_split, DataLoader
from sklearn.utils.class_weight import compute_class_weight
import torch
from torch.optim import AdamW
from tqdm import tqdm
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
import numpy as np
import pandas as pd

/home/lgiordano/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
data = json.load(open('/home/lgiordano/LUCA/CheckThat/annotated_train.json', encoding='utf-8'))

for i in data:
    for ann in i['annotations']:
        start = ann['start']
        end = ann['end']
        print(ann['tag'])
        print(i['text'][int(start):int(end)+1])
        print('----------------------------')

Loaded_Language
 заботы – россий
----------------------------
Loaded_Language
отят возвращаться в Западную Европу: руками, ногами, зубами цепляются, чтобы не возвращаться туда. Предполагает
----------------------------
Name_Calling-Labeling
о-французские надоедливые нахлебники. Идет нар
----------------------------
Appeal_to_Hypocrisy
ся, что они должны получать пособия, а государства наоборот пытаются их вытолкнуть. Люди приехал
----------------------------
Doubt
 модель, где используют очередную порцию мигрантов как дешевую силу. Вторая: 
----------------------------
Loaded_Language
хотят возвращаться в Западную Европу: руками, ногами, зубами цепляются, чтобы не возвращаться туда. Предполагает
----------------------------
Flag_Waving
елать все, чтобы быстро восстанавливать те города, которые сильно пострадали в условиях военных действий. Яркий пример
----------------------------
Name_Calling-Labeling
о-французские надоедливые нахлебники. Идет н
----------------------------
Loaded_Lan

In [ ]:
data = json.load(open('/home/lgiordano/LUCA/CheckThat/annotated_train.json'))
#data = data[:50]

#train_data, val_data = train_test_split(data, test_size=0.2, random_state=42)

tokenizer = XLMRobertaTokenizerFast.from_pretrained('xlm-roberta-base')
label_set = LabelSet(labels=["Appeal_to_Authority", "Appeal_to_Popularity", "Appeal_to_Values", "Appeal_to_Fear-Prejudice", "Flag_Waving",
                             "Causal_Oversimplification", "False_Dilemma-No_Choice", "Consequential_Oversimplification", "Straw_Man",
                             "Red_Herring", "Whataboutism", "Slogans", "Appeal_to_Time", "Conversation_Killer", "Loaded_Language",
                             "Repetition", "Exaggeration-Minimisation", "Obfuscation-Vagueness-Confusion", "Name_Calling-Labeling", "Doubt",
                             "Guilt_by_Association", "Appeal_to_Hypocrisy", "Questioning_the_Reputation"])

data = TrainingDataset(data=data,tokenizer=tokenizer,label_set=label_set)
#train_data, val_data = random_split(data, [round(len(data)*0.8), round(len(data)*0.2)])

train_dataset = TrainingDataset(data=data,tokenizer=tokenizer,label_set=label_set, tokens_per_batch=256)
#val_dataset = TrainingDataset(data=val_data,tokenizer=tokenizer,label_set=label_set, tokens_per_batch=256)

train_loader = DataLoader(train_dataset, collate_fn=TrainingBatch, batch_size=64, shuffle=True)
#val_loader = DataLoader(val_dataset, collate_fn=TrainingBatch, batch_size=64, shuffle=False)

In [ ]:
model = XLMRobertaForTokenClassification.from_pretrained("xlm-roberta-base", num_labels=len(train_dataset.label_set.ids_to_label.values()))
lr = 5e-5
optimizer = AdamW(model.parameters(), lr=lr)
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
epochs = 3

model.to(device)

def train():
    for epoch in range(epochs):
        model.train()
        train_loss = 0
        progbar_train = tqdm(train_loader)
        for i, batch in enumerate(progbar_train):
            optimizer.zero_grad()
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_masks'].to(device)
            labels = batch['labels']

            outputs = model(input_ids=input_ids, attention_mask=attention_mask)
            
            criterion = torch.nn.CrossEntropyLoss(weight=class_weights)

            loss = criterion(outputs['logits'].transpose(1,2), labels.to(device))
            loss.backward()
            train_loss += loss.item()
            
            optimizer.step()

            train_loss_tmp = round(train_loss / (i + 1), 4)
            progbar_train.set_postfix({'Train loss':train_loss_tmp})

        results = evaluate()
        print(results)

def evaluate():
    model.eval()
    eval_loss = 0
    preds = []
    out_label_ids = []

    progbar_val = tqdm(val_loader)
    for i, batch in enumerate(progbar_val):
        with torch.no_grad():
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_masks'].to(device)
            labels = batch['labels'].to(device)

            outputs = model(input_ids=input_ids, attention_mask=attention_mask, labels=labels)

            loss = outputs.loss
            eval_loss += loss.item()

            preds.extend(np.argmax(outputs['logits'].detach().cpu().numpy(), axis=2).flatten())
            out_label_ids.extend(labels.detach().cpu().numpy().flatten())

            val_loss_tmp = round(eval_loss / (i + 1), 4)
            progbar_val.set_postfix({'Eval loss':val_loss_tmp})

    preds = np.array(preds)
    out_label_ids = np.array(out_label_ids)

    results = classification_report(out_label_ids, preds)

    return results

train()

'''en_ar = pd.read_json('/home/pgajo/checkthat24/checkthat24_DIT/data/train/en-ar/annotated_train_translated_nllb-200-3.3B.json').drop(['lang_src', 'text_src'], axis=1).rename(columns={'lang_tgt':'lang', 'text_tgt':'text'})
en_bg = pd.read_json('/home/pgajo/checkthat24/checkthat24_DIT/data/train/en-bg/annotated_train_translated_nllb-200-3.3B.json').drop(['lang_src', 'text_src'], axis=1).rename(columns={'lang_tgt':'lang', 'text_tgt':'text'})
en_es = pd.read_json('/home/pgajo/checkthat24/checkthat24_DIT/data/train/en-es/annotated_train_translated_nllb-200-3.3B.json').drop(['lang_src', 'text_src'], axis=1).rename(columns={'lang_tgt':'lang', 'text_tgt':'text'})
en_it = pd.read_json('/home/pgajo/checkthat24/checkthat24_DIT/data/train/en-it/annotated_train_translated_nllb-200-3.3B.json').drop(['lang_src', 'text_src'], axis=1).rename(columns={'lang_tgt':'lang', 'text_tgt':'text'})
en_it[en_it['lang']=='ita_Latn'] = 'it'
en_po = pd.read_json('/home/pgajo/checkthat24/checkthat24_DIT/data/train/en-po/annotated_train_translated_nllb-200-3.3B.json').drop(['lang_src', 'text_src'], axis=1).rename(columns={'lang_tgt':'lang', 'text_tgt':'text'})
en_ru = pd.read_json('/home/pgajo/checkthat24/checkthat24_DIT/data/train/en-ru/annotated_train_translated_nllb-200-3.3B.json').drop(['lang_src', 'text_src'], axis=1).rename(columns={'lang_tgt':'lang', 'text_tgt':'text'})
en_ru[en_ru['lang']=='rus_Cyrl'] = 'ru'
en_sl = pd.read_json('/home/pgajo/checkthat24/checkthat24_DIT/data/train/en-sl/annotated_train_translated_nllb-200-3.3B.json').drop(['lang_src', 'text_src'], axis=1).rename(columns={'lang_tgt':'lang', 'text_tgt':'text'})'''

#data = pd.concat([original, en_ar, en_bg, en_es, en_it, en_po, en_ru, en_sl], axis=0)

def train():
    for epoch in range(epochs):
        model.train()
        train_loss = 0
        for batch in tqdm(train_loader):
            optimizer.zero_grad()
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_masks'].to(device)
            labels = batch['labels'].to(device)

            outputs = model(input_ids=input_ids, attention_mask=attention_mask)

            loss = criterion(outputs['logits'].transpose(1, 2), labels)
            loss.backward()
            train_loss += loss.item()

            optimizer.step()

        results = evaluate()
        print(results)
    
def evaluate():
    model.eval()
    eval_loss = 0
    preds = None
    out_label_ids = None
    results = {}
    
    for batch in val_loader:
        with torch.no_grad():
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_masks'].to(device)
            labels = batch['labels'].to(device)

            outputs = model(input_ids=input_ids, attention_mask=attention_mask)
            
            loss = criterion(outputs['logits'].transpose(1, 2), labels)
            eval_loss += loss.item()
        
        if preds is None:
            preds = outputs['logits'].detach().cpu().numpy()
            out_label_ids = labels.detach().cpu().numpy()
        else:
            preds = np.append(preds, outputs['logits'].detach().cpu().numpy(), axis=0)
            out_label_ids = np.append(out_label_ids, labels.detach().cpu().numpy(), axis=0)

    preds = np.argmax(preds, axis=2)
    preds = preds.reshape(-1)
    out_label_ids = out_label_ids.reshape(-1)

    result = acc_and_f1_micro(preds, out_label_ids)
    results.update(result)

    return results

train()